In [69]:
import streamlit as st
import folium
from streamlit_folium import st_folium
from geopy.geocoders import Nominatim
import osmnx as ox
import numpy as np 
import matplotlib.pyplot as plt
from folium import GeoJson, GeoJsonTooltip
import geopandas as gpd
from folium.features import GeoJsonPopup
import pandas as pd
from shapely.geometry import Point

In [ ]:

address = "Skaldevägen 60"
POI_radius=500

geolocator = Nominatim(user_agent="Navigator")
location = geolocator.geocode(address)
lat, lon = location.latitude, location.longitude

In [65]:
m = folium.Map(location=[lat, lon], zoom_start=14)


In [66]:
folium.Marker([lat, lon], popup=address, icon=folium.Icon(color='red', icon='home')).add_to(m)
folium.Circle(
         location=[lat, lon],
         radius=POI_radius,  # in meters
         color='blue',       # outline color
         fill=True,
         fill_color='blue',  # fill color
         fill_opacity=0.2,   # transparency (0 = invisible, 1 = opaque)
         weight=2            # outline thickness
         ).add_to(m)



In [ ]:
circle_area =  round(np.pi * POI_radius**2)
circle_area

In [47]:
tags0 = {
    'landuse': True,   # True → all landuse values
    'natural': True,   # all natural features
    'leisure': True,    # all leisure features
    'amenity':True,
    'shop':True,
    'building': True,
}

In [48]:
all_features = ox.features_from_point((lat, lon),tags=tags0, dist=POI_radius)

In [49]:
polygon_features = all_features[all_features.geometry.geom_type.isin(["Polygon", "MultiPolygon"])]
polygon_features

geometry  \
element  id                                                              
relation 4871435     POLYGON ((17.93971 59.32743, 17.94008 59.32751...   
         5120941     POLYGON ((17.9413 59.32953, 17.94126 59.3295, ...   
         5744315     POLYGON ((17.94243 59.32998, 17.94238 59.33011...   
         7015120     POLYGON ((17.93329 59.32404, 17.93349 59.3241,...   
         9680850     POLYGON ((17.93926 59.32994, 17.93969 59.32988...   
...                                                                ...   
way      924657200   POLYGON ((17.93451 59.33008, 17.93457 59.33007...   
         1376130134  POLYGON ((17.92935 59.32918, 17.92941 59.32917...   
         1376133113  POLYGON ((17.9347 59.32835, 17.93463 59.32826,...   
         1408634295  POLYGON ((17.92771 59.33296, 17.92625 59.33284...   
         1408634305  POLYGON ((17.93264 59.33299, 17.93356 59.33291...   

                    amenity cuisine              name addr:city addr:postcode  \
element  id                                                                     
relation 4871435        NaN     NaN      Sångarlunden       NaN           NaN   
         5120941        NaN     NaN  Olovslundsdammen       NaN           NaN   
         5744315        NaN     NaN         Bokhyllan       NaN           NaN   
         7015120        NaN     NaN         Tunadalen       NaN           NaN   
         9680850        NaN     NaN               NaN       NaN           NaN   
...                     ...     ...               ...       ...           ...   
way      924657200      NaN     NaN               NaN       NaN           NaN   
         1376130134     NaN     NaN               NaN    Bromma        167 73   
         1376133113     NaN     NaN               NaN       NaN           NaN   
         1408634295     NaN     NaN               NaN       NaN           NaN   
         1408634305     NaN     NaN               NaN       NaN           NaN   

                     addr:street alt_name brand brand:wikidata  ... wikipedia  \
element  id                                                     ...             
relation 4871435             NaN      NaN   NaN            NaN  ...       NaN   
         5120941             NaN      NaN   NaN            NaN  ...       NaN   
         5744315             NaN      NaN   NaN            NaN  ...       NaN   
         7015120             NaN      NaN   NaN            NaN  ...       NaN   
         9680850             NaN      NaN   NaN            NaN  ...       NaN   
...                          ...      ...   ...            ...  ...       ...   
way      924657200           NaN      NaN   NaN            NaN  ...       NaN   
         1376130134  Skaldevägen      NaN   NaN            NaN  ...       NaN   
         1376133113          NaN      NaN   NaN            NaN  ...       NaN   
         1408634295          NaN      NaN   NaN            NaN  ...       NaN   
         1408634305          NaN      NaN   NaN            NaN  ...       NaN   

                    wikimedia_commons       place surface maxstay  \
element  id                                                         
relation 4871435                  NaN         NaN     NaN     NaN   
         5120941                  NaN         NaN     NaN     NaN   
         5744315                  NaN  city_block     NaN     NaN   
         7015120                  NaN         NaN     NaN     NaN   
         9680850                  NaN         NaN     NaN     NaN   
...                               ...         ...     ...     ...   
way      924657200                NaN         NaN     NaN     NaN   
         1376130134               NaN         NaN     NaN     NaN   
         1376133113               NaN         NaN     NaN     NaN   
         1408634295               NaN         NaN     NaN     NaN   
         1408634305               NaN         NaN     NaN     NaN   

                    building:levels:underground nohousenumber          type  \
element  id   

In [50]:
buildings=all_features[all_features["building"].notna()][["building", "geometry"]]

In [51]:
polygon_features_proj = polygon_features.to_crs(polygon_features.estimate_utm_crs())
polygon_features_proj['area_m2'] = round(polygon_features_proj.geometry.area, 0)


In [52]:
landuse_summary = polygon_features_proj.groupby('landuse')['area_m2'].sum().reset_index()
landuse_summary["prop"] = landuse_summary["area_m2"]/sum(landuse_summary["area_m2"])
landuse_summary

landuse   area_m2      prop
0   allotments    9784.0  0.008201
1       forest  429197.0  0.359739
2        grass   18203.0  0.015257
3   industrial    2823.0  0.002366
4  residential  733072.0  0.614437

In [53]:
industrial= all_features[all_features['landuse'] == 'industrial']

In [63]:
tag_keys = list(tags0.keys())

def detect_key_and_value(row):
    for key in tag_keys:
        if pd.notna(row.get(key)):
            return key, row[key]
    return None, None

all_features['tag_key'], all_features['tag_value'] = zip(*all_features.apply(detect_key_and_value, axis=1))
polygon_features['tag_key'], polygon_features['tag_value'] = zip(*polygon_features.apply(detect_key_and_value, axis=1))


In [67]:
# Create base map
#m = folium.Map(location=[lat, lon], zoom_start=14)

# Plot all polygons with same style
folium.GeoJson(
    data=polygon_features.__geo_interface__,
    style_function=lambda x: {
        'fillColor': 'orange',  # all polygons same color
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.5
    },
     popup=GeoJsonPopup(
        fields=['tag_key', 'tag_value', 'name'],
        aliases=['OSM key:', 'Tag value:', 'Name:']
    )
).add_to(m)
m

In [ ]:
#FUll map code
m = folium.Map(location=[lat, lon], zoom_start=14)

folium.Marker([lat, lon], popup=address, icon=folium.Icon(color='red', icon='home')).add_to(m)
folium.Circle(
         location=[lat, lon],
         radius=POI_radius,  # in meters
         color='blue',       # outline color
         fill=True,
         fill_color='blue',  # fill color
         fill_opacity=0.2,   # transparency (0 = invisible, 1 = opaque)
         weight=2            # outline thickness
         ).add_to(m)

# Plot all polygons with same style
folium.GeoJson(
    data=polygon_features.__geo_interface__,
    style_function=lambda x: {
        'fillColor': 'orange',  # all polygons same color
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.5
    },
     popup=GeoJsonPopup(
        fields=['tag_key', 'tag_value', 'name'],
        aliases=['OSM key:', 'Tag value:', 'Name:']
    )
).add_to(m)
m

In [82]:
circle_gdf

name                                           geometry
0  search_circle  POLYGON ((667537.363 6580317.957, 667534.956 6...

In [83]:
import geopandas as gpd
from shapely.geometry import Point
import folium
from folium.features import GeoJson, GeoJsonPopup

# --- Ensure the polygons have a CRS ---
if polygon_features.crs is None:
    polygon_features = polygon_features.set_crs("EPSG:4326")

# --- 1️⃣ Pick a metric CRS (for buffer in meters) ---
proj_crs = polygon_features.estimate_utm_crs()

# --- 2️⃣ Project both polygons and center point ---
pf_proj = polygon_features.to_crs(proj_crs)
center = gpd.GeoSeries([Point(lon, lat)], crs="EPSG:4326").to_crs(proj_crs).iloc[0]

# --- 3️⃣ Create the circular polygon (real geometry in meters) ---
circle_poly = center.buffer(POI_radius)

# --- 4️⃣ Convert it into a GeoDataFrame ---
circle_gdf = gpd.GeoDataFrame({"geometry": [circle_poly]}, crs=proj_crs)

# --- 5️⃣ CLIP polygons to circle (this is the key part) ---
clipped_proj = gpd.clip(pf_proj, circle_gdf)

# --- 6️⃣ Reproject back to WGS84 for Folium ---
clipped = clipped_proj.to_crs("EPSG:4326")
circle_gdf_wgs = circle_gdf.to_crs("EPSG:4326")

# --- 7️⃣ Build Folium map ---
m = folium.Map(location=[lat, lon], zoom_start=14)

# Center marker and visual circle
folium.Marker([lat, lon], popup=address, icon=folium.Icon(color='red', icon='home')).add_to(m)
folium.Circle(location=[lat, lon], radius=POI_radius,
              color='blue', fill=True, fill_color='blue',
              fill_opacity=0.2, weight=2).add_to(m)

# Add clipped polygons
folium.GeoJson(
    data=clipped.__geo_interface__,
    style_function=lambda x: {
        'fillColor': 'orange',
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.5
    },
    popup=GeoJsonPopup(fields=['tag_key', 'tag_value', 'name'],
                       aliases=['OSM key:', 'Tag value:', 'Name:'])
).add_to(m)

# Add actual circle polygon for visualization
folium.GeoJson(
    data=circle_gdf_wgs.__geo_interface__,
    name="search_circle_polygon",
    style_function=lambda x: {
        "fillColor": "none",
        "color": "blue",
        "weight": 2,
        "dashArray": "5,5"
    }
).add_to(m)

folium.LayerControl().add_to(m)
m
